In [27]:
import pandas as pd
import numpy as np
import warnings 
warnings.filterwarnings("ignore", category=DeprecationWarning)

import spacy
from spacy import displacy
import en_core_web_md

import nltk
from nltk.tokenize import word_tokenize
import matplotlib
%matplotlib inline

In [159]:
combine_df = pd.read_pickle("result.sav")
combine_df.head(3)

id  label                                              tweet  \
0   1    0.0   @user when a father is dysfunctional and is s...   
1   2    0.0  @user @user thanks for #lyft credit i can't us...   
2   3    0.0                                bihday your majesty   

                                         clean_tweet  \
0  when father is dysfunctional and is so selfish...   
1  thanks for lyft credit cannot use cause they d...   
2                                bihday your majesty   

                                     clean_tweet_reg  \
0  when father is dysfunctional and is so selfish...   
1  thanks for lyft credit cannot use cause they d...   
2                                bihday your majesty   

                                         tweet_token  \
0  [when, father, is, dysfunctional, and, is, so,...   
1  [thanks, for, lyft, credit, can, not, use, cau...   
2                            [bihday, your, majesty]   

                                tweet_token_filtered  \
0  [father, dysfunctional, selfish, drags, kids, ...   
1  [thanks, lyft, credit, use, cause, offer, whee...   
2                                  [bihday, majesty]   

                                       tweet_stemmed  \
0  [father, dysfunct, selfish, drag, kid, dysfunc...   
1  [thank, lyft, credit, use, caus, offer, wheelc...   
2                                  [bihday, majesti]   

                                    tweet_lemmatized  
0  [father, dysfunctional, selfish, drag, kid, dy...  
1  [thank, lyft, credit, use, cause, offer, wheel...  
2                                  [bihday, majesty]

#### Задание 1.

Используя библиотеку Spacy, вывести ТОП-20 популярных NER в combine_df датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? (Учтите, что max_word_limit_spacy для Spacy = 1000000)

In [80]:
nlp = en_core_web_md.load()
ny_bb = ' '.join(tweet for tweet in combine_df['clean_tweet'])[:1000000]
article = nlp(ny_bb)
displacy.render(article, jupyter=True, style='ent')

In [183]:
a = []
a1 = []
for ent in article.ents:
    a.append(ent.text)
    a1.append(ent.label_)
    
d = {'text': a, 'label': a1}
df_spacy = pd.DataFrame(data=d)
df_spacy.head()

text   label
0      studiolife aislife     ORG
1                      hp     ORG
2  harrypotter pottermore  PERSON
3               rd bihday     GPE
4               eli ahmir  PERSON

In [184]:
a = df_spacy.groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text     label  count
5757       today      DATE    362
1785       first   ORDINAL    164
1880      friday      DATE    155
4142         one  CARDINAL    137
5783    tomorrow      DATE    137
5794     tonight      TIME    130
4204     orlando       GPE    124
6377      yoyour       GPE    113
5286      sunday      DATE    108
5252      summer      DATE     91
4815    saturday      DATE     81
614       bihday      DATE     76
3645      monday      DATE     76
3239      london       GPE     52
3677     morning      TIME     50
5888         two  CARDINAL     49
179      america       GPE     49
5729    thursday      DATE     45
1711  father day      DATE     34
5960          us       GPE     34

In [185]:
a = df_spacy.groupby(['label']).size().reset_index()
a.columns = ['label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

label  count
13       PERSON   3397
1          DATE   2576
4           GPE   1641
11          ORG   1514
9          NORP    578
16         TIME    503
0      CARDINAL    282
3           FAC    192
10      ORDINAL    188
14      PRODUCT    172
2         EVENT    119
7           LOC    109
17  WORK_OF_ART     79
15     QUANTITY     18
5      LANGUAGE     11
8         MONEY      8
6           LAW      6
12      PERCENT      2

*вывод: если смотреть по частоте, с которой слово встречается в твитах, то самый популярный - DATE, на втором месте ORDINAL.
Если смотреть по частоте, с которой встречается категория, то на первом месте PERSON, на втором DATE*

С помощью Spacy выяснить: какие персоны и организации самые обсуждаемые в train и test датасетах? вывести ТОП-20 самых популярных. Действительно ли в топ вошли только персоны и организации или есть мусор?

In [88]:
train = combine_df[:31962].copy()
train.tail(2)

id  label                                              tweet  \
31960  31961    1.0  @user #sikh #temple vandalised in in #calgary,...   
31961  31962    0.0                   thank you @user for you follow     

                                             clean_tweet  \
31960  sikh temple vandalised in in calgary wso conde...   
31961                           thank you for you follow   

                                             tweet_token  \
31960  [sikh, temple, vandalised, in, in, calgary, ws...   
31961                     [thank, you, for, you, follow]   

                                    tweet_token_filtered  \
31960  [sikh, temple, vandalised, calgary, wso, conde...   
31961                                    [thank, follow]   

                                           tweet_stemmed  \
31960  [sikh, templ, vandalis, calgari, wso, condemn,...   
31961                                    [thank, follow]   

                                        tweet_lemmatized  
31960  [sikh, temple, vandalise, calgary, wso, condem...  
31961                                    [thank, follow]

In [89]:
nlp = en_core_web_md.load()
ny_bb = ' '.join(tweet for tweet in train['clean_tweet'])[:1000000]
article = nlp(ny_bb)

a = []
a1 = []
for ent in article.ents:
    a.append(ent.text)
    a1.append(ent.label_)
    
d = {'text': a, 'label': a1}
df = pd.DataFrame(data=d)

a = df.loc[(df['label']=='PERSON')|(df['label']=='ORG')].groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text   label  count
2700                       obama  PERSON     25
3344                         sta  PERSON     24
934                 deletetweets  PERSON     20
2558                         nba     ORG     19
1433                         gop     ORG     19
3444                       suppo  PERSON     19
1727                       islam     ORG     19
1589                     hillary  PERSON     17
3260                         sjw     ORG     15
467          bing bong bing bong  PERSON     14
4008                     yoyoyou  PERSON     11
2061                      lebron  PERSON     11
477                          bjp  PERSON     11
1191                         fed     ORG     10
761            christina grimmie  PERSON     10
2366  melancholy melancholymusic  PERSON     10
3929                         wso     ORG     10
689                         cavs     ORG      9
3221                         shi  PERSON      9
3940                        xbox  PERSON      9

*вывод - самая обсуждаемая персона obama, самая обсуждаемая организация nba. На мой взгляд в топе есть мусор - deletetweets, bing bong bing bong, yoyoyou, melancholy melancholymusic  и т.д.*

In [90]:
test = combine_df[31962:].copy()
test.head(2)

id  label                                              tweet  \
31962  31963    NaN  #studiolife #aislife #requires #passion #dedic...   
31963  31964    NaN   @user #white #supremacists want everyone to s...   

                                             clean_tweet  \
31962  studiolife aislife requires passion dedication...   
31963  white supremacists want everyone to see the ne...   

                                             tweet_token  \
31962  [studiolife, aislife, requires, passion, dedic...   
31963  [white, supremacists, want, everyone, to, see,...   

                                    tweet_token_filtered  \
31962  [studiolife, aislife, requires, passion, dedic...   
31963  [white, supremacists, want, everyone, see, new...   

                                           tweet_stemmed  \
31962  [studiolif, aislif, requir, passion, dedic, wi...   
31963  [white, supremacist, want, everyon, see, new, ...   

                                        tweet_lemmatized  
31962  [studiolife, aislife, require, passion, dedica...  
31963  [white, supremacists, want, everyone, see, new...

In [91]:
nlp = en_core_web_md.load()
ny_bb = ' '.join(tweet for tweet in test['clean_tweet'])[:1000000]
article = nlp(ny_bb)

a = []
a1 = []
for ent in article.ents:
    a.append(ent.text)
    a1.append(ent.label_)
    
d = {'text': a, 'label': a1}
df = pd.DataFrame(data=d)

a = df.loc[(df['label']=='PERSON')|(df['label']=='ORG')].groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text   label  count
3484                                   suppo  PERSON     28
2736                                   obama  PERSON     24
3385                                     sta  PERSON     22
1413                                     gop     ORG     20
2590                                     nba     ORG     16
1614                                      ht     ORG     14
912                             deletetweets  PERSON     14
1733                                   islam     ORG     13
722                        christina grimmie  PERSON     12
3293                                     sjw     ORG     12
750                                  clinton  PERSON     10
1189  feminismisterrorism feminismmuktbharat  PERSON     10
1849                                  jo cox  PERSON      9
1618                                      hu  PERSON      9
996                             donald trump  PERSON      9
3826                                      wa     ORG      9
517                           bong bing bong  PERSON      9
636                            carl paladino  PERSON      8
593               buffalo simulation buffalo     ORG      8
2096                                  lebron  PERSON      8

*вывод - самая обсуждаемая персона suppo(я так понимаю по контексту suppo это "поддержи, поддержка" и т.д. не персона), obama на втором месте. самая обсуждаемая организация gop, на втором месте nba. На мой взгляд в топе так же есть мусор - suppo, deletetweets, feminismisterrorism feminismmuktbharat,bong bing bong	и т.д.*

In [110]:
for index, row in test.iterrows():
    if 'suppo' in row['tweet_token']:
        print(row['clean_tweet'])
        break

suppo the taiji fisherman no bullying no racism tweet taiji thecove seashepherd


#### Задание 2.

Используя библиотеку nltk, вывести ТОП-20 популярных NER в combine_df датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? Для данного задания используем ограничение на количество символов во входном датасете (max_word_limit_spacy = 1000000), чтобы иметь возможность сравнить результаты работы Spacy и nltk. Обратите внимание, что nltk чувствителен к регистру.

In [171]:
document = ' '.join(tweet for tweet in combine_df['clean_tweet'])[:1000000]
document = document.title()

In [191]:
a = [[' '.join(c[0] for c in chunk), chunk.label() ] for chunk in nltk.ne_chunk(nltk.pos_tag(nltk.word_tokenize(document))) if hasattr(chunk, 'label') ]

In [192]:
df_nltk = pd.DataFrame(data=a)
df_nltk.columns = ['text', 'label']
df_nltk.head()

text         label
0                         Studiolife        PERSON
1           Aislife Requires Passion        PERSON
2                  Find Newmaterials        PERSON
3            White Supremacists Want      FACILITY
4  New Birds Movie And Here Why Safe  ORGANIZATION

In [193]:
a = df_nltk.groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text         label  count
16754                      Yoyou        PERSON    131
16779                     Yoyour           GPE    125
16227                       Will        PERSON     97
10084                        New           GPE     70
15432                         Us           GPE     47
6146                       Happy        PERSON     43
5107                     Forward        PERSON     40
10984                    Orlando           GPE     38
3509                  Delete Old        PERSON     34
2813                        Cold           GPE     33
4578                      Father        PERSON     32
12119                      Ready        PERSON     26
8074                     Libtard        PERSON     24
5624                        Good        PERSON     22
5815                    Grateful        PERSON     22
15609          Vicinity Of Their  ORGANIZATION     22
15546  Vast Expanse Of Mountains  ORGANIZATION     21
8398                         Lot  ORGANIZATION     21
6120                   Happiness  ORGANIZATION     20
1377                        Been        PERSON     20

In [194]:
a = df_nltk.groupby(['label']).size().reset_index()
a.columns = ['label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

label  count
5        PERSON  12370
4  ORGANIZATION   5613
1           GPE   1791
0      FACILITY    434
3      LOCATION     21
2           GSP     14

*вывод: если смотреть по частоте, с которой слово встречается в твитах, то самый популярный - GPE, на втором месте PERSON.
Если смотреть по частоте, с которой встречается категория, то на первом месте PERSON, на втором ORGANIZATION*

С помощью nltk выяснить: какие персоны и организации самые обсуждаемые в train и test датасетах? вывести ТОП-20 самых популярных. Действительно ли в топ вошли только персоны и организации или есть мусор?

In [179]:
train = combine_df[:31962].copy()
train.tail(2)

id  label                                              tweet  \
31960  31961    1.0  @user #sikh #temple vandalised in in #calgary,...   
31961  31962    0.0                   thank you @user for you follow     

                                             clean_tweet  \
31960  sikh temple vandalised in in calgary wso conde...   
31961                           thank you for you follow   

                                         clean_tweet_reg  \
31960  sikh temple vandalised in in calgary wso conde...   
31961                           thank you for you follow   

                                             tweet_token  \
31960  [sikh, temple, vandalised, in, in, calgary, ws...   
31961                     [thank, you, for, you, follow]   

                                    tweet_token_filtered  \
31960  [sikh, temple, vandalised, calgary, wso, conde...   
31961                                    [thank, follow]   

                                           tweet_stemmed  \
31960  [sikh, templ, vandalis, calgari, wso, condemn,...   
31961                                    [thank, follow]   

                                        tweet_lemmatized  
31960  [sikh, temple, vandalise, calgary, wso, condem...  
31961                                    [thank, follow]

In [180]:
document = ' '.join(tweet for tweet in train['clean_tweet'])[:1000000]
document = document.title()

a = [[' '.join(c[0] for c in chunk), chunk.label() ] for chunk in nltk.ne_chunk(nltk.pos_tag(nltk.word_tokenize(document))) if hasattr(chunk, 'label') ]

df = pd.DataFrame(data=a)
df.columns = ['text', 'label']
df.head()

a = df.loc[(df['label']=='PERSON')|(df['label']=='ORG')].groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text   label  count
10479                  Yoyou  PERSON    139
10129                   Will  PERSON     99
2304              Delete Old  PERSON     43
3960                   Happy  PERSON     35
3221                 Forward  PERSON     34
5192                 Libtard  PERSON     33
2955                  Father  PERSON     31
3749                Grateful  PERSON     27
971                     Been  PERSON     27
7890                     Sad  PERSON     26
3560                     Gon  PERSON     20
8863           Strong Source  PERSON     18
6197   Model Love Yoyou Take  PERSON     18
5194     Libtard Sjw Liberal  PERSON     18
4049                    Hard  PERSON     16
7626                   Ready  PERSON     15
3577                    Good  PERSON     15
3757                   Great  PERSON     15
3698       Gorilla Simulator  PERSON     15
4324                     Him  PERSON     14

*вывод - самая обсуждаемая персона Yoyou, самая обсуждаемая организация в топ не вошла. В топе один мусор, реальных персон нет*

In [181]:
test = combine_df[31962:].copy()
test.head(2)

id  label                                              tweet  \
31962  31963    NaN  #studiolife #aislife #requires #passion #dedic...   
31963  31964    NaN   @user #white #supremacists want everyone to s...   

                                             clean_tweet  \
31962  studiolife aislife requires passion dedication...   
31963  white supremacists want everyone to see the ne...   

                                         clean_tweet_reg  \
31962  studiolife aislife requires passion dedication...   
31963  white supremacists want everyone to see the ne...   

                                             tweet_token  \
31962  [studiolife, aislife, requires, passion, dedic...   
31963  [white, supremacists, want, everyone, to, see,...   

                                    tweet_token_filtered  \
31962  [studiolife, aislife, requires, passion, dedic...   
31963  [white, supremacists, want, everyone, see, new...   

                                           tweet_stemmed  \
31962  [studiolif, aislif, requir, passion, dedic, wi...   
31963  [white, supremacist, want, everyon, see, new, ...   

                                        tweet_lemmatized  
31962  [studiolife, aislife, require, passion, dedica...  
31963  [white, supremacists, want, everyone, see, new...

In [182]:
document = ' '.join(tweet for tweet in test['clean_tweet'])[:1000000]
document = document.title()

a = [[' '.join(c[0] for c in chunk), chunk.label() ] for chunk in nltk.ne_chunk(nltk.pos_tag(nltk.word_tokenize(document))) if hasattr(chunk, 'label') ]

df = pd.DataFrame(data=a)
df.columns = ['text', 'label']
df.head()

a = df.loc[(df['label']=='PERSON')|(df['label']=='ORG')].groupby(['text','label']).size().reset_index()
a.columns = ['text', 'label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

text   label  count
10606                  Yoyou  PERSON    131
10223                   Will  PERSON     97
3945                   Happy  PERSON     43
3217                 Forward  PERSON     40
2276              Delete Old  PERSON     34
2960                  Father  PERSON     32
7636                   Ready  PERSON     26
5210                 Libtard  PERSON     24
3577                    Good  PERSON     22
3729                Grateful  PERSON     22
988                     Been  PERSON     20
7918                     Sad  PERSON     19
9586                   Trump  PERSON     18
3569                     Gon  PERSON     18
8943           Strong Source  PERSON     18
6176   Model Love Yoyou Take  PERSON     15
3677       Gorilla Simulator  PERSON     15
5708                Malevote  PERSON     15
9972                    Wait  PERSON     14
4475                     How  PERSON     13

вывод - аналогично, самая обсуждаемая персона Yoyou, самая обсуждаемая организация в топ не вошла. В топе один мусор, единственная реальная персона Trump, и он сильно не на первом месте.

#### Задание 3.

Какая из библиотек по вашему лучше отработала? Сравните качество полученных most_common NER и количество распознаных NER.

**По качеству:** *Если смотреть по топу, то несомненно лучше отработала spacy. nltk чувствительна к регистру. без слов в верхнем регистре она не распознает NER вообще. С примененным методом, когда во всех словах в тексте первые буквы приведены к верхнему регистру - nltk находит очень много мусора.*

**По количеству:** *Аналогично лучше отработала spacy - библиотека нашла 18 различных категорий. nltk только 6*

**Для данного текста, в котором все слова в нижнем регистре, библиотека nltk не подходит.**

In [197]:
a = df_spacy.groupby(['label']).size().reset_index()
a.columns = ['label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.shape

(18, 2)

In [196]:
a = df_nltk.groupby(['label']).size().reset_index()
a.columns = ['label', 'count']
a.sort_values('count', ascending=False, inplace=True)
a.head(20)

label  count
5        PERSON  12370
4  ORGANIZATION   5613
1           GPE   1791
0      FACILITY    434
3      LOCATION     21
2           GSP     14